Seperate from actually formulating the workload, I also spent some time trying to optimize the scalability and performance of the workload, this notebook focuses on those attempts. 

### 1. Install and import dependencies

In [ ]:
!pip install "daft[huggingface,ray]==0.5.21" vllm

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.0/46.0 MB 45.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 414.4/414.4 MB 2.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 169.0/169.0 kB 16.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.5/45.5 kB 4.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 111.0/111.0 kB 12.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.9/3.9 MB 88.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.3/2.3 MB 91.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 821.0/821.0 MB 1.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.5/3.5 MB 95.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.5/7.5 MB 114.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 117.1/117.1 MB 20.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.8/11.8 MB 71.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 571.0/57

 #### Login to HF for access gemma-3n

In [ ]:
!hf auth login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    To log in, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Enter your token (input will not be visible): 
Add token as git credential? (Y/n) 
Token is valid (permission: read).
The token `Anyscale Ray Serve LLM` has been saved to /root/.cache/huggingface/stored_tokens
Cannot authenticate through git-credential as no helper is defined on your machine.
You might have to re-authen

## Online Serving  - Launching the vLLM OpenAI Compatible Server

Run the following in your terminal
```bash
 python -m vllm.entrypoints.openai.api_server \
  --model google/gemma-3n-e4b-it \
  --guided-decoding-backend guidance \
  --dtype bfloat16 \
  --gpu-memory-utilization 0.85 \
  --host 0.0.0.0 --port 8000
```

Note: If you are in Google Colab, you can open a terminal by clicking the terminal icon in the bottom left of the ui.

It usually takes at least **7.5** minutes before the vLLM server is ready


In [ ]:
# Import Dependencies
import asyncio
import base64
import daft
from daft import col, lit
from daft.functions import format, llm_generate
from openai import OpenAI, AsyncOpenAI
import time

# Step 0 Define Variables and Inference UDF ------------------------------------
model_id = 'google/gemma-3n-e4b-it'
api_key = "none"
base_url = "http://0.0.0.0:8000/v1"
client = AsyncOpenAI(api_key=api_key, base_url=base_url)

## Row-Wise UDF

In [ ]:
@daft.func(return_dtype=daft.DataType.string())
async def struct_output_rowwise(model_id: str, text_col: str, image_col: str, extra_body: dict | None = None) -> str:

    content = [{"type": "text", "text": text_col}]
    if image_col:
        content.append({
            "type": "image_url",
            "image_url": {"url": f"data:image/png;base64,{image_col}"},
        })


    result = await client.chat.completions.create(
        messages=[
            {
                "role": "user",
                "content": content
            }
        ],
        model=model_id,
        extra_body=extra_body,
    )
    return result.choices[0].message.content

## Batch UDF

In [ ]:
@daft.udf(return_dtype=daft.DataType.string())
def struct_output_batch(
        model_id: str,
        text_col: daft.Series,
        image_col: daft.Series,
        extra_body: dict | None = None
    ) -> list[str]:


    async def generate(model_id: str, text: str, image: str) -> str:

        content = [{"type": "text", "text": text}]
        if image:
            content.append({
                "type": "image_url",
                "image_url": {"url": f"data:image/png;base64,{image}"},
            })

        result = await client.chat.completions.create(
            messages=[
                {
                    "role": "user",
                    "content": content
                }
            ],
            model=model_id,
            extra_body=extra_body,
        )
        return result.choices[0].message.content

    texts = text_col.to_pylist()
    images = image_col.to_pylist()

    async def gather_completions() -> list[str]:
        tasks = [generate(model_id, t,i) for t,i in zip(texts,images) ]
        return await asyncio.gather(*tasks)

    return asyncio.run(gather_completions())

## Full Model Evaluation Script

In [ ]:
# Step 1 - Load Dataset --------------------------------------------------------
df = daft.read_parquet('hf://datasets/HuggingFaceM4/the_cauldron/ai2d/train-00000-of-00001-2ce340398c113b79.parquet')

# Step 2 - Preprocessing -------------------------------------------------------
# Convert byte string to base64
df = df.explode(col("images")).with_column("image_base64", df["images"].struct.get("bytes").apply(
        lambda x: base64.b64encode(x).decode('utf-8'),
        return_dtype=daft.DataType.string()
    )
)

# Explode Questions
df = df.explode(col("texts")).with_columns({
    "user": df["texts"].struct.get("user"),
    "assistant": df["texts"].struct.get("assistant")
})

# Parse the Question/Answer Strings
df = df.with_columns({
    "question": df["user"]
        .str.extract(r"(?s)Question:\s*(.*?)\s*Choices:")
        .str.replace("Choices:", "")
        .str.replace("Question:",""),
    "choices_string": df["user"]
        .str.extract(r"(?s)Choices:\s*(.*?)\s*Answer?\.?")
        .str.replace("Choices:\n", "")
        .str.replace("Answer",""),
    "answer": df["assistant"]
        .str.extract(r"Answer:\s*(.*)$")
        .str.replace("Answer:",""),
})


# Step 3 - Inference -----------------------------------------------------------
df = df.with_column("result", struct_output_batch(
                                model_id = model_id,
                                text_col = format("{} \n {}", col("question"), col("choices_string")), # Prompt Template
                                image_col = col("image_base64"),
                                extra_body={"guided_choice": ["A", "B", "C", "D"]}
))

# Step 4 - Evaluation ----------------------------------------------------------
df = df.with_column("is_correct", col("result").str.lstrip().str.rstrip() == col("answer").str.lstrip().str.rstrip())


## Materialization ------------------------------------------------------------
start = time.time()
df_eval = df.limit(200).collect() # Limit Num Rows as desired
end = time.time()
num_rows = df_eval.count_rows()
print(f"Processed {num_rows} rows in {end-start} seconds")

🗡️ 🐟 UDF <lambda>: 00:00 

🗡️ 🐟 Project: 00:00 

🗡️ 🐟 Explode: 00:00 

🗡️ 🐟 Parquet Scan: 00:00 

🗡️ 🐟 Explode: 00:00 

...

🗡️ 🐟 Project: 00:00 

🗡️ 🐟 Project: 00:00 

🗡️ 🐟 UDF struct_output_batch: 00:00 

🗡️ 🐟 Project: 00:00 

Processed 200 rows in 15.957581758499146 seconds


Unfortunately, the naive evaluation pipeline doesn't tell us much about the actual performance of the model, or the pipeline.

In [ ]:
# Calculate
pass_fail_rate = df_eval.where(col("is_correct")).count_rows() / df_eval.count_rows()
print(f"Pass/Fail Rate: {pass_fail_rate}")

🗡️ 🐟 InMemorySource: 00:00 

🗡️ 🐟 Project: 00:00 

🗡️ 🐟 Filter: 00:00 

🗡️ 🐟 Count: 00:00 

🗡️ 🐟 Project: 00:00 

Pass/Fail Rate: 0.535


In [ ]:
# Taking a look at the failures:
df_failures = df_eval.select("question","choices_string","answer","result","is_correct","images","image_base64").where(df_eval["is_correct"]==False) \
                    .with_column("image_png", df["images"].struct.get("bytes").image.decode())
df_failures.show()

Ok, the model can definitely see the image. Lets compare the performance of the models across permutations. 

We can also use this opportunity to test how performance changes across different inference methods.

In [ ]:
start = time.time()
df_raw = daft.read_parquet('hf://datasets/HuggingFaceM4/the_cauldron/ai2d/train-00000-of-00001-2ce340398c113b79.parquet').collect()

end = time.time()
num_rows = df_raw.count_rows()
print(f"Processed {num_rows} rows in {end-start} seconds")

🗡️ 🐟 Parquet Scan: 00:00 

Processed 2434 rows in 1.302093505859375 seconds


In [ ]:
# Preprocess the workload just as before, but this time save the lazy df for downstream jobs to reuse pre-materialized.
start = time.time()

df = df_raw.explode(col("images")).with_column("image_base64", df_raw["images"].struct.get("bytes").apply(
        lambda x: base64.b64encode(x).decode('utf-8'),
        return_dtype=daft.DataType.string()
    )
)
df = df.explode(col("texts")).with_columns({
    "user": df["texts"].struct.get("user"),
    "assistant": df["texts"].struct.get("assistant")
})

# Parse the Question/Answer Strings
df_prepped = df.with_columns({
    "question": df["user"]
        .str.extract(r"(?s)Question:\s*(.*?)\s*Choices:")
        .str.replace("Choices:", "")
        .str.replace("Question:",""),
    "choices_string": df["user"]
        .str.extract(r"(?s)Choices:\s*(.*?)\s*Answer?\.?")
        .str.replace("Choices:\n", "")
        .str.replace("Answer",""),
    "answer": df["assistant"]
        .str.extract(r"Answer:\s*(.*)$")
        .str.replace("Answer:",""),
}).collect()


end = time.time()
num_rows = df_prepped.count_rows()
print(f"Processed {num_rows} rows in {end-start} seconds")


🗡️ 🐟 InMemorySource: 00:00 

🗡️ 🐟 Explode: 00:00 

🗡️ 🐟 Project: 00:00 

🗡️ 🐟 UDF <lambda>: 00:00 

🗡️ 🐟 Explode: 00:00 

🗡️ 🐟 Project: 00:00 

🗡️ 🐟 Project: 00:00 

Processed 7462 rows in 2.9510934352874756 seconds


I love how fast preprocessing is. It's not consistent though. I wonder how much of that has to do with the internet connection. If we decouple the huggingface read from the prep, I bet prep becomes consistent....

Yep. Confirmed.

Raw Download:
- Processed 2434 rows in 2.227473258972168 seconds
- Processed 2434 rows in 1.0310463905334473 seconds
- Processed 2434 rows in 1.1237449645996094 seconds
- Processed 2434 rows in 0.8855597972869873 seconds

Preprocessing:
- Processed 7462 rows in 2.7865214347839355 seconds
- Processed 7462 rows in 2.9183526039123535 seconds
- Processed 7462 rows in 2.8689675331115723 seconds


It is concerning how long inference hangs however.

# Inference / Model Performance Evalutation across permutations
- Row-Wise vs Batch UDF (Which one is faster?)
- With/Without Image (Can the model just guess the right answer without the image?)
    - llm_generate on just text
- With/Without Prompt Template (Does the formatting matter?)
- With/Without Extra Body (Does structured outputs matter?)

Analyzing both model accuracy and workload processing time across the entire dataset.

In [ ]:
# 1. Batch UDF (Image + Text + Prompt Template)
start = time.time()
df_batch_udf = df_prepped.with_column("result", struct_output_batch(
                                model_id = model_id,
                                text_col = format("{} \n {}", col("question"), col("choices_string")), # Prompt Template
                                image_col = col("image_base64"),
                                extra_body={"guided_choice": ["A", "B", "C", "D"]}
)).with_column("is_correct", col("result").str.lstrip().str.rstrip() == col("answer").str.lstrip().str.rstrip()).limit(1000).collect()
end = time.time()
num_rows = df_batch_udf.count_rows()
print(f"Batch UDF (Image + Text + Prompt Template) \n Processed {num_rows} rows in {end-start} seconds")

🗡️ 🐟 Limit 1000: 00:00 

🗡️ 🐟 InMemorySource: 00:00 

🗡️ 🐟 Project: 00:00 

🗡️ 🐟 UDF struct_output_batch: 00:00 

🗡️ 🐟 Project: 00:00 

Batch UDF (Image + Text + Prompt Template) 
 Processed 1000 rows in 53.577256202697754 seconds


In [ ]:
df_batch_udf.explain(show_all=True)

Result is cached and will skip computation

* Source:
|   Number of partitions = 4
|   Output schema = images#Struct([Field { name: "bytes", dtype: Binary, metadata:
|     {} }, Field { name: "path", dtype: Utf8, metadata: {} }]), texts#Struct([Field
|     { name: "user", dtype: Utf8, metadata: {} }, Field { name: "assistant",
|     dtype: Utf8, metadata: {} }, Field { name: "source", dtype: Utf8, metadata:
|     {} }]), image_base64#Utf8, user#Utf8, assistant#Utf8, question#Utf8,
|     choices_string#Utf8, answer#Utf8, result#Utf8, is_correct#Boolean

However here is the logical plan used to produce this result:

== Unoptimized Logical Plan ==

* Limit: 1000
|
* Project: col(images), col(texts), col(image_base64), col(user),
|     col(assistant), col(question), col(choices_string), col(answer), col(result),
|     rstrip(lstrip(col(result))) == rstrip(lstrip(col(answer))) as is_correct
|
* Project: col(images), col(texts), col(image_base64), col(user), col(assistant),
|     col(questio

In [ ]:
# Ok so since I can't get 2000 rows to run on the batch_udf as it stands,
# AND I get an error when I add a concurrency param...
# lets turn the batch udf into a class and add a semaphore.

@daft.udf(return_dtype=daft.DataType.string(), concurrency=8)
class StructOutputBatchSemaphore:
    def __init__(self, api_key: str = "none", base_url: str = "http://0.0.0.0:8000/v1", max_conn: int = 48):
        self.client = AsyncOpenAI(api_key=api_key, base_url=base_url)
        self.semaphore = asyncio.Semaphore(max_conn)

    def __call__(self,
            model_id: str,
            text_col: daft.Series,
            image_col: daft.Series,
            extra_body: dict | None = None
        ) -> list[str]:


        async def generate(model_id: str, text: str, image: str) -> str:

            content = [{"type": "text", "text": text}]
            if image:
                content.append({
                    "type": "image_url",
                    "image_url": {"url": f"data:image/png;base64,{image}"},
                })

            result = await client.chat.completions.create(
                messages=[
                    {
                        "role": "user",
                        "content": content
                    }
                ],
                model=model_id,
                extra_body=extra_body,
            )
            return result.choices[0].message.content

        async def infer_with_semaphore(user_text, image):
            async with self.semaphore:
                return await generate(model_id, user_text, image)

        texts = text_col.to_pylist()
        images = image_col.to_pylist()

        async def gather_completions() -> list[str]:
            tasks = [infer_with_semaphore(t,i) for t,i in zip(texts,images) ]
            return await asyncio.gather(*tasks)

        return asyncio.run(gather_completions())


In [ ]:
# 1. Batch UDF (Image + Text + Prompt Template)
struct_batch_class = StructOutputBatchSemaphore(api_key = api_key, base_url = base_url, max_conn=12)
start = time.time()
df_batch_udf = df_prepped.with_column("result", struct_batch_class(
                                model_id = model_id,
                                text_col = format("{} \n {}", col("question"), col("choices_string")), # Prompt Template
                                image_col = col("image_base64"),
                                extra_body={"guided_choice": ["A", "B", "C", "D"]}
)).with_column("is_correct", col("result").str.lstrip().str.rstrip() == col("answer").str.lstrip().str.rstrip()).limit(1000).collect()
end = time.time()
num_rows = df_batch_udf.count_rows()
print(f"Batch UDF (Image + Text + Prompt Template) \n Processed {num_rows} rows in {end-start} seconds")

TypeError: missing a required argument: 'model_id'

In [ ]:
# 2. Rowwise UDF (Image + Text + Full User String (no format expression))
start = time.time()
df_batch_udf_text = df_prepped.with_column("result", struct_output_rowwise(
                                model_id = model_id,
                                text_col = format("{} \n {}", col("question"), col("choices_string")), # Prompt Template
                                image_col = col("image_base64"),
                                extra_body={"guided_choice": ["A", "B", "C", "D"]}
)).with_column("is_correct", col("result").str.lstrip().str.rstrip() == col("answer").str.lstrip().str.rstrip()).limit(1000).collect()
end = time.time()
num_rows = df_batch_udf.count_rows()
print(f"Batch UDF (Image + Text + Full User String) Processed {num_rows} rows in {end-start} seconds")

🗡️ 🐟 Limit 1000: 00:00 

🗡️ 🐟 InMemorySource: 00:00 

🗡️ 🐟 Project: 00:00 

🗡️ 🐟 UDF struct_output_rowwise: 00:00 

🗡️ 🐟 Project: 00:00 

Batch UDF (Image + Text + Full User String) Processed 1000 rows in 43.29086351394653 seconds


In [ ]:
# 3. Row-wise UDF (Text Only)
start = time.time()
df_rowwise_udf = df_prepped.with_column("result", struct_output_rowwise(
                                                    model_id = model_id,
                                                    text_col = col("user"), # No Prompt Template
                                                    image_col = lit(""),
                                                    extra_body={"guided_choice": ["A", "B", "C", "D"]}
)).with_column("is_correct", col("result").str.lstrip().str.rstrip() == col("answer").str.lstrip().str.rstrip()).limit(1000).collect()
end = time.time()
num_rows = df_batch_udf.count_rows()
print(f"Row-wise UDF (Image + Text + Prompt Template) Processed {num_rows} rows in {end-start} seconds")

🗡️ 🐟 UDF struct_output_rowwise: 00:00 

🗡️ 🐟 InMemorySource: 00:00 

ERROR:asyncio:Task exception was never retrieved
future: <Task finished name='Task-7424' coro=<AsyncClient.aclose() done, defined at /usr/local/lib/python3.12/dist-packages/httpx/_client.py:1978> exception=RuntimeError('Event loop is closed')>
Traceback (most recent call last):
  File "/usr/local/lib/python3.12/dist-packages/daft/udf/row_wise.py", line 90, in __call_async_batch
    event_loop = asyncio.get_running_loop()
                 ^^^^^^^^^^^^^^^^^^^^^^^^^^
RuntimeError: no running event loop

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/lib/python3.12/dist-packages/httpx/_client.py", line 1985, in aclose
    await self._transport.aclose()
  File "/usr/local/lib/python3.12/dist-packages/httpx/_transports/default.py", line 406, in aclose
    await self._pool.aclose()
  File "/usr/local/lib/python3.12/dist-packages/httpcore/_async/connection_pool.py", line 353, in aclose
    await self._close_connections

In [ ]:
# 4. Batch UDF (Text Only)
start = time.time()
df_rowwise_udf = df_prepped.with_column("result", struct_output_batch(
                                                    model_id = model_id,
                                                    text_col = col("user"), # No Prompt Template
                                                    image_col = lit(""),
                                                    extra_body={"guided_choice": ["A", "B", "C", "D"]}
                                                )).collect()
end = time.time()
num_rows = df_batch_udf.count_rows()
print(f"Batch UDF (Text Only) Processed {num_rows} rows in {end-start} seconds")

In [ ]:
# 5. llm_generate (Text Only)
start = time.time()
df_rowwise_udf = df_prepped.with_column("result", llm_generate(
                                                    col("user"),
                                                    model = model_id,
                                                    extra_body={"guided_choice": ["A", "B", "C", "D"]}
                                                    api_key = api_key,
                                                    base_url = base_url
                                                )).collect()
end = time.time()
num_rows = df_batch_udf.count_rows()
print(f"Batch UDF (Text Only) Processed {num_rows} rows in {end-start} seconds")